In [4]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
import requests as req
import json
from urllib import parse
from datetime import datetime, timezone
import math
import time
import pymysql
from tqdm import tqdm
import re

In [3]:
# 서머너 네임 db적재
con = pymysql.connect(host='127.0.0.1', user='root', password='root1234',db='riot', charset='utf8')
cur = con.cursor()
num = 1

for save in tqdm(range(100)):
    api_key = "RGAPI-6f4eed01-264c-4333-8a96-fcdafdf28727"
    url = "https://kr.api.riotgames.com/lol/league/v4/entries/RANKED_SOLO_5x5/PLATINUM/II?page="+str(num)
    header = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/106.0.0.0 Safari/537.36",
    "Accept-Language": "ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7",
    "Accept-Charset": "application/x-www-form-urlencoded; charset=UTF-8",
    "Origin": "https://developer.riotgames.com",
    "X-Riot-Token": "RGAPI-6f4eed01-264c-4333-8a96-fcdafdf28727"
    }
    res = req.get(url, headers=header)
    summerner = res.json()
    num += 3
    time.sleep(2)
    for i in summerner:
        summonerName = i['summonerName']
#         print(summonerName)
        sql = "INSERT INTO summerinfo (summernerName) VALUES (%s)"  
        val = (summonerName)
        cur.execute(sql,val)
    con.commit()
cur.close()
con.close()    

100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [04:00<00:00,  2.40s/it]


In [7]:
# 소환사이름으로 puuid 추출함수
def searchId(x) :
    name = x
    enName = parse.quote(name)
#     print(enName)
    api_key = "RGAPI-1ecac1ec-d6b6-40ca-ac71-df39b3114067"
    url = "https://kr.api.riotgames.com/lol/summoner/v4/summoners/by-name/"+enName
    header = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/105.0.0.0 Safari/537.36",
        "Accept-Language": "ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7",
        "Accept-Charset": "application/x-www-form-urlencoded; charset=UTF-8",
        "Origin": "https://developer.riotgames.com",
        "X-Riot-Token": api_key
    }
    res = req.get(url, headers=header)
    search = res.json()
    return search

 

In [15]:
# con = pymysql.connect(host='127.0.0.1', user='root', password='root1234',db='riot', charset='utf8')
# cur = con.cursor()
# sel_sql = "SELECT summernerName FROM summerinfo"
# cur.execute(sel_sql)
# summerner = cur.fetchall()
# print(summerner[0])
# # enName = parse.quote(str(summerner[0]).replace('(','').replace('\'','').replace(',','').replace(')',''))
# # enName2 = parse.quote(str(summerner[0]))
# enName2 = parse.quote(str(summerner[0]))
# print(enName, enName2)

# puuid 추출후 db에 적재
con = pymysql.connect(host='127.0.0.1', user='root', password='root1234',db='riot', charset='utf8')
cur = con.cursor()
sel_sql = "SELECT summernerName FROM summerinfo"
cur.execute(sel_sql)
summerner = cur.fetchall()
for l in tqdm(summerner):
    name = l[0]
    try:
        res = searchId(name)
        puuid = res.get('puuid')
        sql = "UPDATE summerinfo SET puuids= %s where summernerName = %s"
        val = (puuid,name)
        cur.execute(sql,val)
        time.sleep(2)
    except Exception as e:
        print("닉네임"+l+"에서 예외발생")
        print(e)
        time.sleep(120)
    con.commit()
con.close()   

 29%|████████████████████▉                                                    | 5875/20500 [3:50:27<9:33:42,  2.35s/it]


KeyboardInterrupt: 

In [16]:
cur.close()
con.close()

In [8]:
# puuid로 22시즌 랭크매치데이터 가져오기
con = pymysql.connect(host='127.0.0.1', user='root', password='root1234',db='riot', charset='utf8')
cur = con.cursor()
sql = "SELECT puuids FROM summerinfo"
cur.execute(sql)
match = cur.fetchall()
api_key = "RGAPI-1ecac1ec-d6b6-40ca-ac71-df39b3114067"
start= str(int(datetime(2022, 1, 8).replace(tzinfo=timezone.utc).timestamp()))
end = str(int(datetime(2022, 11, 9).replace(tzinfo=timezone.utc).timestamp()))
for m in tqdm(match):
#     print(m[0])
    startCount = 0
    totalCount = 100
    url = 'https://asia.api.riotgames.com/lol/match/v5/matches/by-puuid/'+str(m[0])+'/ids?startTime='+start+'&endTime='+end+'&type=ranked&start='+str(startCount)+'&count='+str(totalCount)
    header = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/106.0.0.0 Safari/537.36",
        "Accept-Language": "ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7",
        "Accept-Charset": "application/x-www-form-urlencoded; charset=UTF-8",
        "Origin": "https://developer.riotgames.com",
        "X-Riot-Token": api_key
    }
    try :
        res = req.get(url, headers=header)
        matchId = res.json()
        time.sleep(2)
        for index, i in enumerate(matchId) :
            insert = "INSERT INTO matchId (matchId) VALUES ( %s )"
            val = i
            cur.execute(insert, val)
    except Exception as e:
        print("puuid"+i+"의"+index+" 행에서 예외발생")
        print(e)
        time.sleep(120)
    con.commit()
cur.close()
con.close()

100%|████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

wLN3njg8mGAgRPQxx0dHZF25z-DGEZ0WOBVDtUzbCKY6ofWH7o3oQFkW5cCT9Jh-wbb-QXK9ptAdFQ


## 인게임데이터 불러오기

In [2]:
# DB테이블 DataFrame으로 변경
con = pymysql.connect(host='127.0.0.1', user='root', password='root1234',db='riot', charset='utf8')
# cur = con.cursor()
#cur.execute("select * from addata")
import pandas as pd
topdata = pd.read_sql("describe topdata", con, index_col='Field')
jgdata = pd.read_sql("describe jgdata", con, index_col='Field')
middata = pd.read_sql("describe middata", con, index_col='Field')
addata = pd.read_sql("describe addata", con, index_col='Field')
supdata = pd.read_sql("describe supdata", con, index_col='Field')
topdata,jgdata,middata,addata,supdata

D:\kdigital\anaconda\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
D:\kdigital\anaconda\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
D:\kdigital\anaconda\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
D:\kdigital\anaconda\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 conne

(                       Type Null  Key Default           Extra
 Field                                                        
 tno                     int   NO  PRI    None  auto_increment
 blue_top_champ  varchar(45)  YES         None                
 bt_kill                 int  YES         None                
 bt_gold                 int  YES         None                
 bt_damageDone           int  YES         None                
 bt_damageTaken          int  YES         None                
 bt_level                int  YES         None                
 bt_minion               int  YES         None                
 red_top_champ   varchar(45)  YES         None                
 rt_kill                 int  YES         None                
 rt_gold                 int  YES         None                
 rt_damageDone           int  YES         None                
 rt_damageTaken          int  YES         None                
 rt_level                int  YES         None         

In [ ]:
#15분 이전 블루팀 스펙(insert)챔프이름,블루킬,블루골드,블루딜량,블루탱량,블루렙,블루미니언,승리
insert = "INSERT INTO %s (%s,%s,%s,%s,%s,%s,%s,%s,%s) VALUES (%s,'%s',%s,%s,%s,%s,%s,%s,%s)"
#15분 이전 레드팀 스펙(update) 테이블명,챔프이름,레드킬,레드골드,레드딜량,레드탱량,레드렙,레드미니언,no
update = "UPDATE %s SET %s='%s',%s=%d,%s=%d,%s=%s,%s=%s,%s=%d,%s=%s WHERE %s=%s"

#DB테이블의 no를 유동적으로 변경하기 위해 리스트로 선언
noList = ['tno','jno','mno','ano','sno']

#DB테이블 명을 유동적으로 변경하기 위해 리스트로 선언
position = ['topdata','jgdata','middata','addata','supdata']

#챔피언명 리스트로반환
champList = []

#포지션별 no 인덱스
tindex=jindex=mindex=aindex=sindex = 29550

#킬count를 담을 변수 선언
bt=bj=bm=ba=bs=rt=rj=rm=ra=rs = 0

#승리팀(True,False) 구분
winList = []
winSep = 3

# #matchid 가져오기
con = pymysql.connect(host='127.0.0.1', user='root', password='root1234',db='riot', charset='utf8')
cur = con.cursor()
sql = 'SELECT matchId FROM matchid'
cur.execute(sql)
getMatchId = cur.fetchall()
api_key = 'RGAPI-c5fdb499-2dd4-4360-ad47-e3411fdfe66b'
header = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/106.0.0.0 Safari/537.36",
    "Accept-Language": "ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7",
    "Accept-Charset": "application/x-www-form-urlencoded; charset=UTF-8",
    "Origin": "https://developer.riotgames.com",
    "X-Riot-Token": api_key
}
for matchId in tqdm(getMatchId):
#     print(type(matchId[0]))
#     일반매치데이터 호출
    try:
        orgUrl = 'https://asia.api.riotgames.com/lol/match/v5/matches/'+matchId[0]+'?api_key='+api_key
        orgMatch = req.get(orgUrl, headers=header)
        orgData = orgMatch.json()

        #타임라인매치데이터 호출
        timeUrl = 'https://asia.api.riotgames.com/lol/match/v5/matches/'+matchId[0]+'/timeline?api_key='+api_key
        timeMatch = req.get(timeUrl,headers=header)
        timeData = timeMatch.json()
    except Exception as e:
        print(matchId[0]+" 호출중 예외발생")
        print(e)
        time.sleep(5)
    try:
        sampledata = orgData['info']['participants']
        if len(timeData['info']['frames']) > 15:
            sampledata2 = timeData['info']['frames'][15]['participantFrames']
            #데이터전처리 후 db적재
            for winResult in sampledata:
                winList.append(winResult['win'])
                if winList[0] == True:
                    winSep = 0
                else :
                    winSep = 1
            #     print(winSep)
            for champName in sampledata:
            #     print(champName['championName'])
                champList.append(champName['championName'])
            for timeline in range(1,16):
                for count in timeData['info']['frames'][timeline]['events']:
                    if count.get('type') == 'CHAMPION_KILL':
            #             print(count['killerId'])
                        if count['killerId'] == 1:
                            bt+=1
                        if count['killerId'] == 2:
                            bj+=1
                        if count['killerId'] == 3:
                            bm+=1
                        if count['killerId'] == 4:
                            ba+=1
                        if count['killerId'] == 5:
                            bs+=1
                        if count['killerId'] == 6:
                            rt+=1
                        if count['killerId'] == 7:
                            rj+=1
                        if count['killerId'] == 8:
                            rm+=1
                        if count['killerId'] == 9:
                            ra+=1
                        if count['killerId'] == 10:
                            rs+=1
            for i in range(1,11):
                if i == 1:
            #             print('블루탑')#no,챔프이름,블루킬,블루골드,블루딜량,블루탱량,블루렙,블루미니언,승리
                    bt_level = sampledata2[str(i)]['level']
                    bt_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    bt_totalGold = sampledata2[str(i)]['totalGold']
                    bt_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    bt_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_bt = (position[0],noList[0],topdata.index[1],topdata.index[2],topdata.index[3],topdata.index[4],topdata.index[5],topdata.index[6],topdata.index[7],topdata.index[15],
                        tindex,champList[0],bt,bt_totalGold,bt_totalDamageDoneToChampions,bt_totalDamageTaken,bt_level,bt_minionsKilled,winSep)
                    print(var_bt)
                    cur.execute(insert % var_bt)
                if i == 2:
            #             print('블루정글')
                    bj_level = sampledata2[str(i)]['level']
                    bj_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    bj_totalGold = sampledata2[str(i)]['totalGold']
                    bj_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    bj_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_bj = (position[1],noList[1],jgdata.index[1],jgdata.index[2],jgdata.index[3],jgdata.index[4],jgdata.index[5],jgdata.index[6],jgdata.index[7],jgdata.last_valid_index(),
                        jindex,champList[1],bj,bj_totalGold,bj_totalDamageDoneToChampions,bj_totalDamageTaken,bj_level,bj_minionsKilled,winSep)
                    print(var_bj)
                    cur.execute(insert % var_bj)
                if i == 3:
            #             print('블루미드')
                    bm_level = sampledata2[str(i)]['level']
                    bm_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    bm_totalGold = sampledata2[str(i)]['totalGold']
                    bm_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    bm_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_bm = (position[2],noList[2],middata.index[1],middata.index[2],middata.index[3],middata.index[4],middata.index[5],middata.index[6],middata.index[7],middata.last_valid_index(),
                        mindex,champList[2],bm,bm_totalGold,bm_totalDamageDoneToChampions,bm_totalDamageTaken,bm_level,bm_minionsKilled,winSep)
                    print(var_bm)
                    cur.execute(insert % var_bm)
                if i == 4:
            #             print('블루원딜')
                    ba_level = sampledata2[str(i)]['level']
                    ba_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    ba_totalGold = sampledata2[str(i)]['totalGold']
                    ba_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    ba_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_ba = (position[3],noList[3],addata.index[1],addata.index[2],addata.index[3],addata.index[4],addata.index[5],addata.index[6],addata.index[7],addata.last_valid_index(),
                        aindex,champList[3],ba,ba_totalGold,ba_totalDamageDoneToChampions,ba_totalDamageTaken,ba_level,ba_minionsKilled,winSep)
                    print(var_ba)
                    cur.execute(insert % var_ba)
                if i == 5:
            #             print('블루서폿')
                    bs_level = sampledata2[str(i)]['level']
                    bs_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    bs_totalGold = sampledata2[str(i)]['totalGold']
                    bs_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    bs_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_bs = (position[4],noList[4],supdata.index[1],supdata.index[2],supdata.index[3],supdata.index[4],supdata.index[5],supdata.index[6],supdata.index[7],supdata.last_valid_index(),
                        sindex,champList[4],bs,bs_totalGold,bs_totalDamageDoneToChampions,bs_totalDamageTaken,bs_level,bs_minionsKilled,winSep)
                    print(var_bs)
                    cur.execute(insert % var_bs)
                if i == 6: #'UPDATE %s SET %s=%s,%s=%s,%s=%s,%s=%s,%s=%s,%s=%s,%s=%s WHERE %s=%s' 테이블명,챔프이름,레드킬,레드골드,레드딜량,레드탱량,레드렙,레드미니언,no
            #             print('레드탑')
                    rt_level = sampledata2[str(i)]['level']
                    rt_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    rt_totalGold = sampledata2[str(i)]['totalGold']
                    rt_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    rt_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_rt = (position[0],topdata.index[8],champList[5],topdata.index[9],rt,topdata.index[10],rt_totalGold,topdata.index[11],rt_totalDamageDoneToChampions,
                          topdata.index[12],rt_totalDamageTaken,topdata.index[13],rt_level,topdata.index[14],rt_minionsKilled,noList[0],tindex)
                    print(var_rt)
                    cur.execute(update % var_rt)
                if i == 7:
            #             print('레드정글')
                    rj_level = sampledata2[str(i)]['level']
                    rj_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    rj_totalGold = sampledata2[str(i)]['totalGold']
                    rj_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    rj_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_rj = (position[1],jgdata.index[8],champList[6],jgdata.index[9],rj,jgdata.index[10],rj_totalGold,jgdata.index[11],rt_totalDamageDoneToChampions,
                          jgdata.index[12],rj_totalDamageTaken,jgdata.index[13],rj_level,jgdata.index[14],rj_minionsKilled,noList[1],jindex)
                    print(var_rj)
                    cur.execute(update % var_rj)
                if i == 8:
            #             print('레드미드')
                    rm_level = sampledata2[str(i)]['level']
                    rm_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    rm_totalGold = sampledata2[str(i)]['totalGold']
                    rm_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    rm_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_rm = (position[2],middata.index[8],champList[7],middata.index[9],rm,middata.index[10],rm_totalGold,middata.index[11],rm_totalDamageDoneToChampions,
                          middata.index[12],rm_totalDamageTaken,middata.index[13],rm_level,middata.index[14],rm_minionsKilled,noList[2],mindex)
                    print(var_rm)
                    cur.execute(update % var_rm)
                if i == 9:
            #             print('레드원딜')
                    ra_level = sampledata2[str(i)]['level']
                    ra_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    ra_totalGold = sampledata2[str(i)]['totalGold']
                    ra_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    ra_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_ra = (position[3],addata.index[8],champList[8],addata.index[9],ra,addata.index[10],ra_totalGold,addata.index[11],ra_totalDamageDoneToChampions,
                          addata.index[12],ra_totalDamageTaken,addata.index[13],ra_level,addata.index[14],ra_minionsKilled,noList[3],aindex)
                    print(var_ra)
                    cur.execute(update % var_ra)
                if i == 10:
            #             print('레드서폿')
                    rs_level = sampledata2[str(i)]['level']
                    rs_minionsKilled = sampledata2[str(i)]['minionsKilled']
                    rs_totalGold = sampledata2[str(i)]['totalGold']
                    rs_totalDamageDoneToChampions = sampledata2[str(i)]['damageStats']['totalDamageDoneToChampions']
                    rs_totalDamageTaken = sampledata2[str(i)]['damageStats']['totalDamageTaken']
                    var_rs = (position[4],supdata.index[8],champList[9],supdata.index[9],rs,supdata.index[10],rs_totalGold,supdata.index[11],rs_totalDamageDoneToChampions,
                          supdata.index[12],rs_totalDamageTaken,supdata.index[13],rs_level,supdata.index[14],rs_minionsKilled,noList[4],sindex)
                    print(var_rs)
                    cur.execute(update % var_rs)
                con.commit()
            time.sleep(5)
            tindex+=1
            jindex+=1
            mindex+=1
            aindex+=1
            sindex+=1
            #초기화
            bt=bj=bm=ba=bs=rt=rj=rm=ra=rs = 0
            champList = []
            winList = []
            winSep = 3
#             time.sleep(1)
    except Exception as e:
        print(matchId[0]+" db적재 중 예외발생")
        print(e)
cur.close()
con.close()

  0%|                                                                                       | 0/498346 [00:00<?, ?it/s]

('topdata', 'tno', 'blue_top_champ', 'bt_kill', 'bt_gold', 'bt_damageDone', 'bt_damageTaken', 'bt_level', 'bt_minion', 'result', 19466, 'Darius', 3, 7089, 4296, 6562, 11, 131, 1)
('jgdata', 'jno', 'blue_jg_champ', 'bj_kill', 'bj_gold', 'bj_damageDone', 'bj_damageTaken', 'bj_level', 'bj_minion', 'result', 19466, 'Kayn', 5, 6362, 6232, 14877, 10, 8, 1)
('middata', 'mno', 'blue_mid_champ', 'bm_kill', 'bm_gold', 'bm_damageDone', 'bm_damageTaken', 'bm_level', 'bm_minion', 'result', 19466, 'Ryze', 2, 6143, 5991, 5631, 11, 130, 1)
('addata', 'ano', 'blue_ad_champ', 'bad_kill', 'bad_gold', 'bad_damageDone', 'bad_damageTaken', 'bad_level', 'bad_minion', 'result', 19466, 'Aphelios', 4, 6219, 8949, 7940, 8, 87, 1)
('supdata', 'sno', 'blue_sup_champ', 'bs_kill', 'bs_gold', 'bs_damageDone', 'bs_damageTaken', 'bs_level', 'bs_minion', 'result', 19466, 'Thresh', 1, 3753, 2777, 8796, 7, 15, 1)
('topdata', 'red_top_champ', 'JarvanIV', 'rt_kill', 1, 'rt_gold', 4906, 'rt_damageDone', 3307, 'rt_damageTaken

  0%|                                                                           | 1/498346 [00:05<822:04:31,  5.94s/it]

('topdata', 'tno', 'blue_top_champ', 'bt_kill', 'bt_gold', 'bt_damageDone', 'bt_damageTaken', 'bt_level', 'bt_minion', 'result', 19467, 'Jax', 0, 4343, 5426, 9185, 10, 83, 0)
('jgdata', 'jno', 'blue_jg_champ', 'bj_kill', 'bj_gold', 'bj_damageDone', 'bj_damageTaken', 'bj_level', 'bj_minion', 'result', 19467, 'Qiyana', 1, 5027, 3044, 11091, 9, 18, 0)
('middata', 'mno', 'blue_mid_champ', 'bm_kill', 'bm_gold', 'bm_damageDone', 'bm_damageTaken', 'bm_level', 'bm_minion', 'result', 19467, 'Sylas', 3, 5399, 7301, 10017, 10, 98, 0)
('addata', 'ano', 'blue_ad_champ', 'bad_kill', 'bad_gold', 'bad_damageDone', 'bad_damageTaken', 'bad_level', 'bad_minion', 'result', 19467, 'Lucian', 8, 7872, 10983, 9105, 9, 113, 0)
('supdata', 'sno', 'blue_sup_champ', 'bs_kill', 'bs_gold', 'bs_damageDone', 'bs_damageTaken', 'bs_level', 'bs_minion', 'result', 19467, 'Nami', 2, 5874, 3346, 6327, 8, 7, 0)
('topdata', 'red_top_champ', 'Rengar', 'rt_kill', 5, 'rt_gold', 7144, 'rt_damageDone', 10381, 'rt_damageTaken', 98

  0%|                                                                           | 2/498346 [00:11<819:30:13,  5.92s/it]

...

('topdata', 'tno', 'blue_top_champ', 'bt_kill', 'bt_gold', 'bt_damageDone', 'bt_damageTaken', 'bt_level', 'bt_minion', 'result', 21454, 'Mordekaiser', 1, 4707, 3401, 9070, 11, 97, 1)
('jgdata', 'jno', 'blue_jg_champ', 'bj_kill', 'bj_gold', 'bj_damageDone', 'bj_damageTaken', 'bj_level', 'bj_minion', 'result', 21454, 'Graves', 3, 6609, 6118, 7687, 10, 22, 1)
('middata', 'mno', 'blue_mid_champ', 'bm_kill', 'bm_gold', 'bm_damageDone', 'bm_damageTaken', 'bm_level', 'bm_minion', 'result', 21454, 'TwistedFate', 0, 5378, 4074, 4848, 10, 116, 1)
('addata', 'ano', 'blue_ad_champ', 'bad_kill', 'bad_gold', 'bad_damageDone', 'bad_damageTaken', 'bad_level', 'bad_minion', 'result', 21454, 'Sivir', 2, 5314, 5430, 7824, 8, 99, 1)
('supdata', 'sno', 'blue_sup_champ', 'bs_kill', 'bs_gold', 'bs_damageDone', 'bs_damageTaken', 'bs_level', 'bs_minion', 'result', 21454, 'Taric', 1, 3985, 1735, 4898, 8, 26, 1)
('topdata', 'red_top_champ', 'Teemo', 'rt_kill', 1, 'rt_gold', 5433, 'rt_damageDone', 9550, 'rt_damag

  0%|▎                                                                     | 2015/498346 [4:48:09<805:03:27,  5.84s/it]

('topdata', 'tno', 'blue_top_champ', 'bt_kill', 'bt_gold', 'bt_damageDone', 'bt_damageTaken', 'bt_level', 'bt_minion', 'result', 21455, 'Gnar', 2, 4514, 10236, 8249, 10, 81, 0)
('jgdata', 'jno', 'blue_jg_champ', 'bj_kill', 'bj_gold', 'bj_damageDone', 'bj_damageTaken', 'bj_level', 'bj_minion', 'result', 21455, 'MonkeyKing', 2, 5095, 4320, 13344, 9, 4, 0)
('middata', 'mno', 'blue_mid_champ', 'bm_kill', 'bm_gold', 'bm_damageDone', 'bm_damageTaken', 'bm_level', 'bm_minion', 'result', 21455, 'Kassadin', 1, 5792, 6862, 7410, 11, 129, 0)
('addata', 'ano', 'blue_ad_champ', 'bad_kill', 'bad_gold', 'bad_damageDone', 'bad_damageTaken', 'bad_level', 'bad_minion', 'result', 21455, 'Caitlyn', 5, 6574, 6211, 5915, 9, 109, 0)
('supdata', 'sno', 'blue_sup_champ', 'bs_kill', 'bs_gold', 'bs_damageDone', 'bs_damageTaken', 'bs_level', 'bs_minion', 'result', 21455, 'Morgana', 1, 4092, 4463, 5985, 8, 10, 0)
('topdata', 'red_top_champ', 'Warwick', 'rt_kill', 4, 'rt_gold', 6114, 'rt_damageDone', 7380, 'rt_dama

  0%|▎                                                                     | 2016/498346 [4:48:15<815:56:26,  5.92s/it]

('topdata', 'tno', 'blue_top_champ', 'bt_kill', 'bt_gold', 'bt_damageDone', 'bt_damageTaken', 'bt_level', 'bt_minion', 'result', 21456, 'Renekton', 0, 5098, 3847, 8324, 10, 122, 0)
('jgdata', 'jno', 'blue_jg_champ', 'bj_kill', 'bj_gold', 'bj_damageDone', 'bj_damageTaken', 'bj_level', 'bj_minion', 'result', 21456, 'Nidalee', 7, 7552, 6969, 11572, 9, 4, 0)
('middata', 'mno', 'blue_mid_champ', 'bm_kill', 'bm_gold', 'bm_damageDone', 'bm_damageTaken', 'bm_level', 'bm_minion', 'result', 21456, 'Ahri', 5, 6980, 8498, 6464, 10, 116, 0)
('addata', 'ano', 'blue_ad_champ', 'bad_kill', 'bad_gold', 'bad_damageDone', 'bad_damageTaken', 'bad_level', 'bad_minion', 'result', 21456, 'Ashe', 2, 5535, 5700, 6026, 9, 96, 0)
('supdata', 'sno', 'blue_sup_champ', 'bs_kill', 'bs_gold', 'bs_damageDone', 'bs_damageTaken', 'bs_level', 'bs_minion', 'result', 21456, 'Morgana', 2, 4917, 3935, 3769, 8, 11, 0)
('topdata', 'red_top_champ', 'Gnar', 'rt_kill', 0, 'rt_gold', 5083, 'rt_damageDone', 6011, 'rt_damageTaken', 

In [57]:
cur.close()
con.close()